# 데이터, 패키지 로드

In [13]:
# 패키지
import pandas as pd 
import sys # clova sentiment
import requests # clova sentiment
import json # clova sentiment
import numpy as np

In [14]:
# 데이터 로드 
news1 = pd.read_excel("../../../data/News/news_summary_under.xlsx") # 2000자 이내라 clova summary를 적용한 요약문 데이터 
news2 = pd.read_excel("../../../data/News/news_summary_over.xlsx") # 2000자 넘어서 summa로 줄인 데이터 

In [15]:
news1.head(1) # 확인 

NEWS_YM        DATE_TIME  WRITER SUBCATEGORY                       TITLE  \
0   202301  20230102_084347  eDaily          사회  BTS 자리 넘본다…유망주는 스트레이 키즈-KB   

   IMPORTANCE ITEM_NAME                                  TAG_LIST  \
0       67.91       NaN  BTS| 판매량| NCT| 넥스트| 엔하이픈| 블랙핑크| 에스파| 아이브   

                                      PARSED CONTENT  LENGTH_SUM  \
0  - KB증권 “군 입대 BTS에 도전 이어질 것”- “스트레이 키즈, 군 이슈 없고...        1713   

                                             SUMMARY  
0  방탄소년단(BTS)을 이을 아이돌 그룹에 스트레이 키즈가 유력하다는 전망이 제기됐습...

In [16]:
news2.head(1) # 확인 

NEWS_YM        DATE_TIME  WRITER SUBCATEGORY  \
0   202301  20230102_100838  eDaily          기술   

                            TITLE  IMPORTANCE  ITEM_NAME TAG_LIST  \
0  [특징주]와이지엔터, 베이비몬스터 데뷔 예고에 6%대↑       68.31  와이지엔터테인먼트     블랙핑크   

                                      PARSED CONTENT  LENGTH_SUM  \
0  [이데일리 이정현 기자] 신인 걸그룹 공개를 예고한 와이지엔터테인먼트(122870)...        2424   

                                             SUMMARY  LENGTH_SUMMARY  
0  신인 걸그룹 공개를 예고한 와이지엔터테인먼트(122870)가 2일 장초반 강세다.마...              30

In [17]:
# 불필요한 열 'LENGTH_SUMMARY'(=제목+본문 글자수) 삭제
news2 = news2.drop('LENGTH_SUMMARY', axis=1)

In [18]:
# 삭제되었는지 확인
news2.head(1)

NEWS_YM        DATE_TIME  WRITER SUBCATEGORY  \
0   202301  20230102_100838  eDaily          기술   

                            TITLE  IMPORTANCE  ITEM_NAME TAG_LIST  \
0  [특징주]와이지엔터, 베이비몬스터 데뷔 예고에 6%대↑       68.31  와이지엔터테인먼트     블랙핑크   

                                      PARSED CONTENT  LENGTH_SUM  \
0  [이데일리 이정현 기자] 신인 걸그룹 공개를 예고한 와이지엔터테인먼트(122870)...        2424   

                                             SUMMARY  
0  신인 걸그룹 공개를 예고한 와이지엔터테인먼트(122870)가 2일 장초반 강세다.마...

In [19]:
news = pd.concat([news1, news2], ignore_index=True) # 세로로 합쳐 전체 요약문 데이터프레임 생성

In [20]:
# 확인
news.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2935 entries, 0 to 2934
Data columns (total 11 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   NEWS_YM         2935 non-null   int64  
 1   DATE_TIME       2935 non-null   object 
 2   WRITER          2935 non-null   object 
 3   SUBCATEGORY     2935 non-null   object 
 4   TITLE           2935 non-null   object 
 5   IMPORTANCE      2935 non-null   float64
 6   ITEM_NAME       1596 non-null   object 
 7   TAG_LIST        2253 non-null   object 
 8   PARSED CONTENT  2935 non-null   object 
 9   LENGTH_SUM      2935 non-null   int64  
 10  SUMMARY         2935 non-null   object 
dtypes: float64(1), int64(2), object(8)
memory usage: 252.4+ KB


# 요약문 전처리 
## 에러 있는 요약문 처리
- SUMMARY(요약문) 변수에 Error 메세지 있는 경우 SUMMARY 값을 PARSED CONTENT(기사 원문)로 대체

In [21]:
# SUMMARY(요약문) 변수에 Error 메세지 있는 경우 SUMMARY 값을 PARSED CONTENT(기사 원문)로 대체
error_mask = news['SUMMARY'].str.startswith('Error :')
news.loc[error_mask, 'SUMMARY'] = news.loc[error_mask, 'PARSED CONTENT']

In [22]:
# 요약문이 'Error :' 로 시작하는 행의 개수 
news['SUMMARY'].str.startswith('Error :').sum()

0

## 요약문 재생성 
- CLOVA SENTIMENT 는 1000자 이내의 글에 대해서만 실행가능함 
- 이미 요약된 내용을 다시 CLOVA SUMMARY에 넣어 글자수를 축소함
- 3문장으로 요약하도록 파라미터를 설정

In [23]:
# 기본 변수 세팅
#!/usr/bin/env python3
#-*- codig: utf-8 -*-
client_id = "5bgb8zehd8"
client_secret = "yunrcvpfGN1Lrw8TR1X8xTxt8Eem1fJGX4EzRoaT"
headers = {
    "X-NCP-APIGW-API-KEY-ID": client_id,
    "X-NCP-APIGW-API-KEY": client_secret,
    "Content-Type": "application/json"
}
language = "ko" # Language of document (ko, ja )
model = "news" # Model used for summaries (general, news)
tone = "2" # Converts the tone of the summarized result. (0, 1, 2, 3)
summaryCount = "3" # This is the number of sentences for the summarized document.
url= "https://naveropenapi.apigw.ntruss.com/text-summary/v1/summarize" 

# 요약문 생성 함수
def generate_summary(df, language, model, tone, summaryCount):

    def generate_single_summary(row):
        content = row['SUMMARY'] # SUMMARY 변수의 내용을 요약한다
        title = row['TITLE']

        data = {
            "document": {
                "title": title,
                "content": content
            },
            "option": {
                "language": language,
                "model": model,
                "tone": tone,
                "summaryCount": summaryCount
            }
        }

        response = requests.post(url, data=json.dumps(data), headers=headers)
        rescode = response.status_code
        if rescode == 200:
            summary = json.loads(response.text)["summary"]
            return summary
        else:
            return "Error : " + response.text
    
    df['SUMMARY_2'] = df.apply(generate_single_summary, axis=1) # SUMMARY 변수의 내용을 요약한 결과를 SUMMARY_2 변수에 저장
    return df


In [24]:
# 요약문 생성 함수 적용
result_dataframe = generate_summary(news, language, model, tone, summaryCount)

In [25]:
# 결과 확인
result_dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2935 entries, 0 to 2934
Data columns (total 12 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   NEWS_YM         2935 non-null   int64  
 1   DATE_TIME       2935 non-null   object 
 2   WRITER          2935 non-null   object 
 3   SUBCATEGORY     2935 non-null   object 
 4   TITLE           2935 non-null   object 
 5   IMPORTANCE      2935 non-null   float64
 6   ITEM_NAME       1596 non-null   object 
 7   TAG_LIST        2253 non-null   object 
 8   PARSED CONTENT  2935 non-null   object 
 9   LENGTH_SUM      2935 non-null   int64  
 10  SUMMARY         2935 non-null   object 
 11  SUMMARY_2       2935 non-null   object 
dtypes: float64(1), int64(2), object(9)
memory usage: 275.3+ KB


## 에러 있는 요약문 처리
- SUMMARY(요약문) 변수에 Error 메세지 있는 경우 SUMMARY 값을 PARSED CONTENT(기사 원문)로 대체

In [26]:
# SUMMARY_2(재생성한 요약문) 변수에 Error 메세지 있는 경우 SUMMARY_2 값을 PARSED CONTENT(기사 원문)로 대체
error_mask = result_dataframe['SUMMARY_2'].str.startswith('Error :')
result_dataframe.loc[error_mask, 'SUMMARY_2'] = result_dataframe.loc[error_mask, 'SUMMARY']

In [27]:
# news 데이터프레임에 저장 
news = result_dataframe

# CLOVA SENTIMENT(감정분석)

## (테스팅)요약문 하나에 대해 감정분석 적용해보기

In [28]:
news['SUMMARY_2'].iloc[1000] # 테스팅할 요약문

'SM엔터테인먼트 현 경영진이 경쟁사 하이브와 경영권 분쟁을 벌이고 있는 가운데 소액주주들에게 서한을 보내 지지를 호소했습니다.\n특히 SM은 하이브와 업계 최대 경쟁사임을 강조하며 부정적 측면이 발생할 수 있다는 주장을 펼치기도 했다.SM은 "좋은 연습생도, 좋은 곡도, 좋은 안무가와 공연 기획도 모두 하이브가 SM에 가지는 지분율보다 더 높은 지분율을 가진 빅히트(방탄소년단 소속사), 어도어(뉴진스 소속사), 쏘스뮤직(르세라핌 소속사), 플레디스(세븐틴 소속사) 같은 산하 레이블에 먼저 배정할 수밖에 없다"고 했습니다.\n또 "하이브가 SM 지분을 최대 40%까지만 보유하고 나머지 60%는 일반 주주들이 가지게 되면 SM 주주와 하이브 주주 사이에는 이해 상충이 발생할 수밖에 없다"고 주장하기도 했습니다.'

In [29]:
# 기본 세팅
#!/usr/bin/env python3
#-*- codig: utf-8 -*-
import sys
import requests
import json
client_id = "5bgb8zehd8"
client_secret = "yunrcvpfGN1Lrw8TR1X8xTxt8Eem1fJGX4EzRoaT"
url="https://naveropenapi.apigw.ntruss.com/sentiment-analysis/v1/analyze"
headers = {
    "X-NCP-APIGW-API-KEY-ID": client_id,
    "X-NCP-APIGW-API-KEY": client_secret,
    "Content-Type": "application/json"
}

# 감정 분석 진행 
content = news['SUMMARY_2'].iloc[1000]  # SUMMARY_2 변수에 대해 진행 
data = {
  "content": content
}
print(json.dumps(data, indent=4, sort_keys=True))
response = requests.post(url, data=json.dumps(data), headers=headers)
rescode = response.status_code
if(rescode == 200):
    print (response.text)
else:
    print("Error : " + response.text)

{
    "content": "SM\uc5d4\ud130\ud14c\uc778\uba3c\ud2b8 \ud604 \uacbd\uc601\uc9c4\uc774 \uacbd\uc7c1\uc0ac \ud558\uc774\ube0c\uc640 \uacbd\uc601\uad8c \ubd84\uc7c1\uc744 \ubc8c\uc774\uace0 \uc788\ub294 \uac00\uc6b4\ub370 \uc18c\uc561\uc8fc\uc8fc\ub4e4\uc5d0\uac8c \uc11c\ud55c\uc744 \ubcf4\ub0b4 \uc9c0\uc9c0\ub97c \ud638\uc18c\ud588\uc2b5\ub2c8\ub2e4.\n\ud2b9\ud788 SM\uc740 \ud558\uc774\ube0c\uc640 \uc5c5\uacc4 \ucd5c\ub300 \uacbd\uc7c1\uc0ac\uc784\uc744 \uac15\uc870\ud558\uba70 \ubd80\uc815\uc801 \uce21\uba74\uc774 \ubc1c\uc0dd\ud560 \uc218 \uc788\ub2e4\ub294 \uc8fc\uc7a5\uc744 \ud3bc\uce58\uae30\ub3c4 \ud588\ub2e4.SM\uc740 \"\uc88b\uc740 \uc5f0\uc2b5\uc0dd\ub3c4, \uc88b\uc740 \uace1\ub3c4, \uc88b\uc740 \uc548\ubb34\uac00\uc640 \uacf5\uc5f0 \uae30\ud68d\ub3c4 \ubaa8\ub450 \ud558\uc774\ube0c\uac00 SM\uc5d0 \uac00\uc9c0\ub294 \uc9c0\ubd84\uc728\ubcf4\ub2e4 \ub354 \ub192\uc740 \uc9c0\ubd84\uc728\uc744 \uac00\uc9c4 \ube45\ud788\ud2b8(\ubc29\ud0c4\uc18c\ub144\ub2e8 \uc18c\uc18d\uc0ac), \uc

- 감정지수가 잘 나오므로 함수를 생성하여 전체 기사에 대해 적용

## 뉴스기사 요약문 전체에 대해 감성분석 적용

In [30]:
# 기본 세팅
#!/usr/bin/env python3

client_id = "5bgb8zehd8"
client_secret = "yunrcvpfGN1Lrw8TR1X8xTxt8Eem1fJGX4EzRoaT"
url="https://naveropenapi.apigw.ntruss.com/sentiment-analysis/v1/analyze"
headers = {
    "X-NCP-APIGW-API-KEY-ID": client_id,
    "X-NCP-APIGW-API-KEY": client_secret,
    "Content-Type": "application/json"
}


# 데이터프레임 생성
columns = ['SENTIMENT_NEGATIVE', 'SENTIMENT_NEUTRAL', 'SENTIMENT_POSITIVE'] # 감정 분석 결과를 데이터프레임에 추가할 열 이름
sent = pd.DataFrame(columns=columns) # 감정 분석 결과를 저장할 데이터프레임

for i in range(len(news)):
    content = news['SUMMARY_2'].iloc[i] # 감성분석할 내용 : news 데이터의 SUMMARY_2 내용 전체 
    data = {
      "content": content
    }
    print(json.dumps(data, indent=4, sort_keys=True))
    response = requests.post(url, data=json.dumps(data), headers=headers)
    rescode = response.status_code
    if(rescode == 200):
        print (response.text)
        response_data = json.loads(response.text)
        A = response_data["document"]["confidence"]["negative"] # 각 요약문의 부정지수 
        B = response_data["document"]["confidence"]["neutral"] # 각 요약문의 중립지수 
        C = response_data["document"]["confidence"]["positive"] # 각 요약문의 긍정지수 
        sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
        # 부정지수, 중립지수, 긍정지수를 각각 sent 데이터프레임의 SENTIMENT_NEGATIVE, SENTIMENT_NEUTRAL, SENTIMENT_POSITIVE 변수에 저장
        
    else:
        print("Error : " + response.text) 
        sent = sent.append({'SENTIMENT_NEGATIVE': np.nan, 'SENTIMENT_NEUTRAL': np.nan, 'SENTIMENT_POSITIVE': np.nan}, ignore_index=True)
        # 감정분석 결과가 산출되지 않는 경우 각 변수에 np.nan 값을 할당
        

{
    "content": "\ubc29\ud0c4\uc18c\ub144\ub2e8(BTS)\uc744 \uc774\uc744 \uc544\uc774\ub3cc \uadf8\ub8f9\uc5d0 \uc2a4\ud2b8\ub808\uc774 \ud0a4\uc988\uac00 \uc720\ub825\ud558\ub2e4\ub294 \uc804\ub9dd\uc774 \uc81c\uae30\ub410\uc2b5\ub2c8\ub2e4.\n\uc774\uc120\ud654 KB\uc99d\uad8c \uc560\ub110\ub9ac\uc2a4\ud2b8\uc640 \ub958\uc740\uc560 \uc5f0\uad6c\uc6d0\uc740 2\uc77c '\uc5f0\ucc28\ubcc4 \ud310\ub9e4\ub7c9\uc73c\ub85c \ubcf8 2023 \uc720\ub9dd\uc8fc' \ubcf4\uace0\uc11c\uc5d0\uc11c \"BTS\uc758 \uad70 \uc785\ub300\ub85c \uc778\ud574 BTS\uc758 \uc644\uc804\uccb4 \ud65c\ub3d9\uc774 \ubd88\uac00\ub2a5\ud574\uc9c0\uba74\uc11c 2023\ub144\uc5d0\ub294 K\ud31d\uc758 \uc5ed\uc0ac\ub97c \uc368 \ub0b4\ub824\uc628 BTS\uc758 \uae30\ub85d\uc744 \uae68\ub824\ub294 \ubcf4\uc774\uadf8\ub8f9\ub4e4\uc758 \ub3c4\uc804\uc774 \uc774\uc5b4\uc9c8 \uac83\"\uc774\ub77c\uba70 \"\ub125\uc2a4\ud2b8 BTS\ub85c \uac00\uc7a5 \uc720\ub9dd\ud55c \uc544\ud2f0\uc2a4\ud2b8\ub294 \uc2a4\ud2b8\ub808\uc774 \ud0a4\uc988\"\ub77c\uace0

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)


{
    "content": "\ubc29\ud0c4\uc18c\ub144\ub2e8(BTS) \uad70 \uc785\ub300\uc5d0\ub3c4 K\ud31d \uc568\ubc94\uacfc \uc8fc\uac00\uac00 \uc120\ubc29\ud560 \uac83\uc774\ub780 \uc804\ub9dd\uc774 \uc81c\uae30\ub410\uc2b5\ub2c8\ub2e4.\n\uc774 \uc5f0\uad6c\uc6d0\uc740 \"\ubc29\ud0c4\uc18c\ub144\ub2e8 \uadf8\ub8f9 \ud65c\ub3d9 \uc911\ub2e8\uc73c\ub85c \uc778\ud55c \uc568\ubc94 \ud310\ub9e4\ub7c9 \uac10\uc18c\ub294 \ucd5c\ub300 300\ub9cc\uc7a5 \uc218\uc900\uc77c \uac83\"\uc774\ub77c\uba70 \"\uc21c\ucc28\uc801\uc778 \uad70\uc785\ub300 \uc77c\uc815\uc73c\ub85c \ubc29\ud0c4\uc18c\ub144\ub2e8 \uadf8\ub8f9 \ud65c\ub3d9\uc740 \uc57d 2\ub144\uac04 \uc911\ub2e8\ub420 \uac83\uc774\ub098, \uac1c\ubcc4 \uc2e0\uaddc \uc568\ubc94 \ud65c\ub3d9\uc740 \uc5f0\uac04 \ucd5c\uc18c 3\ud68c \uc9c4\ud589 \uc608\uc815\uc73c\ub85c, \ubc29\ud0c4\uc18c\ub144\ub2e8\uc758 \ucf54\uc5b4 \ud32c\ub364(50\ub9cc~70\ub9cc\uba85 \ucd94\uc0b0) \uc218\ub97c \uac10\uc548\ud560 \uc2dc \uc2e0\uaddc \uc568\ubc94 \ud310\ub9e4\ub7c9\ub9cc \

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)


{"document":{"sentiment":"positive","confidence":{"negative":33.33496,"positive":66.63944,"neutral":0.025600519}},"sentences":[{"content":"지난해 연말 코스피 약세장 속에서 나홀로 '산타랠리'를 이어갔던 엔터주가 새해 들어서도 승승장구하고 있습니다.","offset":0,"length":61,"sentiment":"positive","confidence":{"negative":0.0013202326,"positive":0.997974,"neutral":7.058217E-4},"highlights":[{"offset":36,"length":20}]},{"content":"\n중국 당국은 최근 한국 게임 7개에 대해 중국 내 서비스를 허가하는 등 한한령을 완화할 조짐을 보이고 있습니다.","offset":61,"length":63,"sentiment":"positive","confidence":{"negative":0.0012283736,"positive":0.9967849,"neutral":0.00198665},"highlights":[{"offset":43,"length":15}]},{"content":"\n엔터 업종의 경우 2017년 한한령이 실시된 이후 중국에서 공연을 열지 못하고 있습니다.","offset":124,"length":50,"sentiment":"negative","confidence":{"negative":0.9977441,"positive":3.4030626E-4,"neutral":0.0019156217},"highlights":[{"offset":1,"length":44}]}]}
{
    "content": "\uba54\ub9ac\uce20\uc99d\uad8c\uc740 \uc640\uc774\uc9c0\uc5d4\ud130\ud14c\uc778\uba3c\ud2b8(122870)\uc5d0 \ub300\ud574 \"\ub

...

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)


{"document":{"sentiment":"positive","confidence":{"negative":0.0998906,"positive":95.69983,"neutral":4.2002826}},"sentences":[{"content":"멤버 슈가가 올해 4월 발표한 첫 공식 솔로 음반 'D-데이'(D-DAY)는 빌보드 메인 앨범 차트 '빌보드 200'에서 131위를 기록하며 5주 연속 머물렀습니다.","offset":0,"length":92,"sentiment":"neutral","confidence":{"negative":0.011874287,"positive":0.44534764,"neutral":0.5427781},"highlights":[{"offset":82,"length":9}]},{"content":"\n그룹 세븐틴은 미니 10집 'FML'로 '빌보드 200'에서 44위로 4주째 자리를 지켰으며 '월드 앨범' 차트 2위, '톱 커런트 앨범 세일즈'와 '톱 앨범 세일즈' 차트에서 각각 5위를 차지했습니다.","offset":92,"length":114,"sentiment":"positive","confidence":{"negative":4.7622283E-4,"positive":0.9978557,"neutral":0.0016680604},"highlights":[{"offset":95,"length":18}]},{"content":"\n그룹 (여자)아이들의 미니 6집 '아이 필'(I Feel)은 이번 주 '빌보드 200' 차트에 41위로 새로 진입했으며, 음반 타이틀곡 '퀸카'는 '글로벌 200' 차트에서 지난주 157위보다 대폭 오른 38위를 기록했습니다.","offset":206,"length":127,"sentiment":"positive","confidence":{"negative":6.35267E-4,"positive":0.99777406,"neutral":0.0015906102},"highlights":[{"offset":93,

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)


{"document":{"sentiment":"positive","confidence":{"negative":0.011313287,"positive":92.29237,"neutral":7.6963096}},"sentences":[{"content":"동명의 타이틀곡 '언포기븐'은 '글로벌 200' 72위, '글로벌(미국 제외)' 39위에 올랐습니다.","offset":0,"length":56,"sentiment":"neutral","confidence":{"negative":1.09751476E-4,"positive":0.0014450795,"neutral":0.9984452},"highlights":[{"offset":45,"length":10}]},{"content":"\n세븐틴은 미니 10 집 'FML'로 124위에 오르며 7주째 진입에 성공했으며 타이틀곡 '손오공'은 '글로벌 200' 103위를 기록했습니다.","offset":56,"length":80,"sentiment":"positive","confidence":{"negative":5.590459E-4,"positive":0.99809045,"neutral":0.0013505456},"highlights":[{"offset":21,"length":29}]},{"content":"\n올해 데뷔 10주년을 맞은 그룹 방탄소년단(BTS)의 단체곡 '테이크 투'(TAKE TWO)는 별다른 음반 활동 없이도 메인 싱글 차트 '핫100'에 48위로 진입했으며 '글로벌 200' 차트에서는 1위에 올랐습니다.","offset":136,"length":122,"sentiment":"positive","confidence":{"negative":8.019299E-4,"positive":0.9984736,"neutral":7.245093E-4},"highlights":[{"offset":106,"length":15}]}]}
{
    "content": "\uc81c\ubaa9 : \uc99d\uc2dc\uc694\

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/266010802.py:37: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': np.nan, 'SENTIMENT_NEUTRAL': np.nan, 'SENTIMENT_POSITIVE': np.nan}, ignore_index=True)


In [31]:
# 감정분석 결과 데이터프레임 확인
sent.info() 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2935 entries, 0 to 2934
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   SENTIMENT_NEGATIVE  2886 non-null   object
 1   SENTIMENT_NEUTRAL   2886 non-null   object
 2   SENTIMENT_POSITIVE  2886 non-null   object
dtypes: object(3)
memory usage: 68.9+ KB


In [32]:
# 감정분석 결과 데이터프레임 확인
sent.tail(2) 

SENTIMENT_NEGATIVE SENTIMENT_NEUTRAL SENTIMENT_POSITIVE
2933           0.011313           7.69631           92.29237
2934                NaN               NaN                NaN

In [33]:
# news에 감성지수 데이터프레임(sent) 합치기
news = pd.concat([news, sent], axis=1)
news.head(2) # 확인

NEWS_YM        DATE_TIME  WRITER SUBCATEGORY                       TITLE  \
0   202301  20230102_084347  eDaily          사회  BTS 자리 넘본다…유망주는 스트레이 키즈-KB   
1   202301  20230104_082655  eDaily          경제   BTS 군입대에도 K팝 주가 선방 전망-IBK   

   IMPORTANCE ITEM_NAME                                  TAG_LIST  \
0       67.91       NaN  BTS| 판매량| NCT| 넥스트| 엔하이픈| 블랙핑크| 에스파| 아이브   
1       67.81       NaN              판매량| 방탄소년단| BTS| 개별| 공연| 글로벌   

                                      PARSED CONTENT  LENGTH_SUM  \
0  - KB증권 “군 입대 BTS에 도전 이어질 것”- “스트레이 키즈, 군 이슈 없고...        1713   
1  - 이환욱 “K팝 앨범 판매 증가, 하이브 주가 상향”[이데일리 최훈길 기자] 방탄...        1887   

                                             SUMMARY  \
0  방탄소년단(BTS)을 이을 아이돌 그룹에 스트레이 키즈가 유력하다는 전망이 제기됐습...   
1  방탄소년단(BTS) 군 입대에도 K팝 앨범과 주가가 선방할 것이란 전망이 제기됐습니...   

                                           SUMMARY_2 SENTIMENT_NEGATIVE  \
0  방탄소년단(BTS)을 이을 아이돌 그룹에 스트레이 키즈가 유력하다는 전망이 제기됐습...           0.013367   
1  방탄소년단(BTS) 군 입대에도 K팝 앨범과 주가가 선방할 것이란 전망이 제기됐습니...          32.145016   

  SENTIMENT_NEUTRAL SENTIMENT_POSITIVE  
0          7.872859           92.11378  
1           1.13692           66.71806

- 감성지수가 결측치인 행이 총 49개 존재

## 감성지수 결측치 처리
### 감성지수가 결측인 행/결측이 아닌 행 분리 

- news 데이터프레임에서 SENTIMENT_POSITIVE 값이 결측치인 행과 그렇지 않은 행을 분리
- 각각 news_nan, news_no_nan 이름의 데이터프레임에 저장 

In [34]:
news_nan = news[news['SENTIMENT_POSITIVE'].isna()] # 감정지수 결측치 존재하는 데이터 
news_no_nan = news[~news['SENTIMENT_POSITIVE'].isna()]  # 감정지수 결측치 없는 데이터 

In [35]:
# 확인
news_nan.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 49 entries, 86 to 2934
Data columns (total 15 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   NEWS_YM             49 non-null     int64  
 1   DATE_TIME           49 non-null     object 
 2   WRITER              49 non-null     object 
 3   SUBCATEGORY         49 non-null     object 
 4   TITLE               49 non-null     object 
 5   IMPORTANCE          49 non-null     float64
 6   ITEM_NAME           41 non-null     object 
 7   TAG_LIST            29 non-null     object 
 8   PARSED CONTENT      49 non-null     object 
 9   LENGTH_SUM          49 non-null     int64  
 10  SUMMARY             49 non-null     object 
 11  SUMMARY_2           49 non-null     object 
 12  SENTIMENT_NEGATIVE  0 non-null      object 
 13  SENTIMENT_NEUTRAL   0 non-null      object 
 14  SENTIMENT_POSITIVE  0 non-null      object 
dtypes: float64(1), int64(2), object(12)
memory usage: 6.1+ K

In [36]:
# 결측치 존재하는 데이터의 TITLE 확인
news_nan['TITLE'].head(49)

86                          [애널리스트에게 듣는다] 2023년 엔터·콘텐츠 전망
217                                 오후장 기술적 분석 특징주 B(코스피)
313                                    증시요약(2) - 코스닥 마감시황
317                           증시요약(8) - 기술적 분석 특징주 B(코스피)
476                                 [백전무패] 공시로 풀어보는 기업 분석
653                                 오전장 기술적 분석 특징주 B(코스피)
935                                              오후장★테마동향
1273        [오늘의 증시 리포트] “와이지엔터테인먼트, 혼자 저평가 받기에는 탁월환 성장률"
1274                        [오늘의증시] 롯데에너지머티리얼즈·하이브·대한해운 등
1406                              [애널리스트에게 듣는다] K-엔터주의 질주
1424    [주식선생 '일타'] 자동차 실적 선방 하이닉스 충격 미미, 파월 이번에는 금리 인...
1532                                             오전장★테마동향
1638                             [공시로 보는 주가] 투자 아이디어를 찾아라
1949                                        오전장 특징주★(코스닥)
1950                                             오전장★테마동향
1951                                             오전장★테마동향
1952                                      증시요약(3) - 특징 테마
1954          

- 감성변수가 결측치인 행들의 TITLE(기사 제목)을 확인해본 결과,
- 오전장★테마동향, 오전장 특징주★(코스닥), 증시요약, .. 등과 같은 "여러 종목의 시황을 종합적으로 정리해주는" 기사임을 확인하였음 
- 이런 기사들의 경우 분야별, 종목별로 '다양한' 내용을 다루기에 긍정/부정을 판단하기 어려움
- 뿐만 아니라, 엔터주 자체의 주가를 예측하는 데에도 유용하게 사용되기 힘듦
- **따라서 아래의 인덱스에 해당하는 기사들을** *****제외한***** **나머지는 "삭제"하기로 결정**
    - 86, 1273, 1406, 2469, 2543, 2702, 2741,2862

### 감정지수에 결측치가 있는 뉴스 중 엔터주 주가예측과 유관한 뉴스만 추출

In [37]:
news_nan = news_nan.loc[[86, 1273, 1406, 2468, 2542, 2701, 2740,2861]]
news_nan.head(2)

NEWS_YM        DATE_TIME WRITER SUBCATEGORY  \
86     202301  20230116_152329   매일경제          경제   
1273   202303  20230321_080021   이투데이          경제   

                                              TITLE  IMPORTANCE  \
86                    [애널리스트에게 듣는다] 2023년 엔터·콘텐츠 전망       40.76   
1273  [오늘의 증시 리포트] “와이지엔터테인먼트, 혼자 저평가 받기에는 탁월환 성장률"       28.26   

                            ITEM_NAME TAG_LIST  \
86                                NaN  콘텐츠| 일본   
1273  오리온홀딩스|SK하이닉스|LG생활건강|인터로조|현대모비스      NaN   

                                         PARSED CONTENT  LENGTH_SUM  \
86    2023년 엔터·콘텐츠 전망Q. 카카오엔터, 에스엠 인수 탄력 받나?A. 사우디 국...        1249   
1273   ◇현대모비스 2022년 물류비가 7,677억원 증가했었다최근 2년간 외형 성장은 ...        1639   

                                                SUMMARY  \
86    2023년 엔터·콘텐츠 전망Q. 카카오엔터, 에스엠 인수 탄력 받나?A. 사우디 국...   
1273   ◇현대모비스 2022년 물류비가 7,677억원 증가했었다최근 2년간 외형 성장은 ...   

                                              SUMMARY_2 SENTIMENT_NEGATIVE  \
86    2023년 엔터·콘텐츠 전망Q. 카카오엔터, 에스엠 인수 탄력 받나?A. 사우디 국...                NaN   
1273   ◇현대모비스 2022년 물류비가 7,677억원 증가했었다최근 2년간 외형 성장은 ...                NaN   

     SENTIMENT_NEUTRAL SENTIMENT_POSITIVE  
86                 NaN                NaN  
1273               NaN                NaN

### SUMMARY_2 내용 확인 및 전처리

#### (1)

In [38]:
news_nan['SUMMARY_2'].iloc[0] 

"2023년 엔터·콘텐츠 전망Q. 카카오엔터, 에스엠 인수 탄력 받나?A. 사우디 국부펀드 6천억+싱가포르 자금 6천억 유치A. 콘텐츠 기업 해외 투자 유치 사례 중 최대 규모A. K-콘텐츠 산업 가능성 세계적 인정 받아A. 지난 12일 카카오엔터 유상증자 공시A. 기타법인 취득 자금 목적으로 유상증자 결정Q. 디어유, 유니버스 인수 기대감은?A. 하이브?'위버스', 월간활성이용자수(MAU) 700만명 육박A. 유니버스 흡수로 60% 수준 신규 아티스트 증가할 것A. 강력한 팬덤 확보 아티스트의 버블 서비스 시작 기대A. 아이브·몬스타엑스·에이티즈·더보이즈 등 A. 중국 안드로이드 진출 + 일본 아티스트 영입 모멘텀Q. YG엔터 양현석 복귀 기대감은?A. 블랙핑크, 투어 끝내고 솔로 활동 체제 후 다시 완전체A. 트레저, 지난주까지 일본 투어 성황리에 마쳐A. 1월 말 돔사이즈 오사카에서 앵콜콘 추가A. 3월에 아시아 투어 들어갈 예정A. 신인 걸그룹 '베몬', 완성도 더하는 마지막 단계Q. 하이브 추가 상승 모멘텀은?A. 12 뉴진스 초동 70만장 판매A. 투바투 미니앨범 선주문량 150만장 이상 판매A. 3월 말에 투어 예정…작년 2배 이상 규모 월드투어A. 세븐틴, 일본 위주 활동할 것Q. JYP Ent. 올해 실적 전망은?A. 2023년 매출 4,840억·영업익 1,341억 예상A. 1) 2023 신인 네 팀 데뷔A. 2) 아티스트 IP 활용 다각화A. 3) JYP 360, 글로벌 활동에 맞춰 마진 내재화A. 아티스트 팬덤 북미·일본 중심 확대A. 아티스트 IP 활용한 비즈니스 포트폴리오 다각화 강화A. 관심종목 : 하이브·와이지엔터테인먼트안진아 이베스트투자증권 리서치센터 미디어엔터 애널리스트 by 매일경제TV                                                                                                                                          

- 하나의 이슈를 다루지 않기에 감성평가가 불가능한 형태
- *****삭제*****

In [39]:
index_to_drop = news_nan.index[0]
news_nan = news_nan.drop(index_to_drop)

#### (2)

In [40]:
news_nan['SUMMARY_2'].iloc[0] 

' ◇현대모비스 2022년 물류비가 7,677억원 증가했었다최근 2년간 외형 성장은 이익 증가를 견인하지 못한 성장최근 2년 이익률 하락에는 물류비 증가가 큰 영향2023년~2024년 물류비 감소하면서 비용부담 완화송선재 하나증권 연구원 ◇대명에너지 돈버는 재생에너지 발전기업재생에너지 전문 발전 사업자우호적인 영업환경, 진입장벽 높은 풍력발전 사업2023년 실적 매출액 1218억원과 영업이익 365억 원 전망안주원 DS투자증권 연구원 ◇오리온홀딩스 한 단계 성장하는 구간신 사업부 확대투자의견 매수, 목표주가 21,000원으로 조사분석 개시남성현 IBK투자증권 연구원 ◇비나텍 비나이다 비나이다 수주 소식을 비나기업개요: 글로벌 친환경 에너지 소재·부품 전문 기업FY22 연결 매출액 706.6억원 (+44.3% YoY), 영업이익 93.5억원 (+66.2% YoY)체크포인트: 1) 사용처가 다양해지는 슈퍼커패시터2) 수소연료전지 CAPA 확대 임박리스크 요인: 오버행 이슈김현겸 KB증권 연구원 ◇인터로조 매출 성장과 밸류에이션 상향 요인 확보2022년 실적은 예상 하회2023년 실적은 성장 기대중국과 미국은 밸류에이션 상향 요인권명준 유안타증권 연구원 ◇KT서브마린 모든 해저케이블은 서브마린으로 통한다LS전선과 해상풍력용 해저전력케이블 시너지 극대화 기대올해 실적 턴어라운드 예상, 고부가 전력선 중심 성장김지산 키움증권 연구원 ◇동국제강 새로운 시작을 앞두다인적분할 앞두고 있어2023년, 열연(후판&봉형강) - 다소 흐림, 냉연 - 회귀지주회사 전환은 긍정적, 2개의 사업회사 분할 효과는 지켜봐야이현수 유안타증권 연구원 ◇SK이노베이션 2023년 1분기 실적 부진 대비해야!1분기 예상 영업이익 1,516억원, 컨센 이하배터리 2분기 미국 IRA 보조금 효과는 긍정적그러나,         목표주가 25만원으로 하향황규원 유안타증권 연구원 ◇제이시스메디칼 기대되는 중국 진출 & 성공 Story2023년에도 성장 이상 無중국 진출을 주목해야 하는 이유목표주가 10,00

- 엔터주 주가예측과 무관한 내용 
- *****삭제*****

In [41]:
index_to_drop = news_nan.index[0]
news_nan = news_nan.drop(index_to_drop)

#### (3)

In [42]:
news_nan['SUMMARY_2'].iloc[0] 

"▶ K-엔터주의 질주Q. 빨갛게 달아오른 엔터주, 왜?A. 아티스트 활동 모멘텀A. 새로운 시장 확장 및 펀더멘탈 개선 기대Q. 시총 3조 돌파한 JYP Ent. 실적 전망은?A. 컨센서스 부합하는 무난한 실적 전망Q. 경영권 분쟁 겪은 에스엠, 전망은?A. 1분기는 다소 아쉬운 실적 예상A. 2분기부터 아티스트 활동에 따른 상승 기대Q. BTS 군입대에도 견조한 하이브, 상승 기대할까?A. 뉴진스 등 주요 아티스트 활동 A. 위버스 등의 모멘텀 더해져 상승 기대Q. 와이지엔터 향후 전망은?A. 신인 아티스트 컴백 기대감 유효Q. 오를 만큼 오른 엔터주 투자 전략은?A. 최선호주: 하이브(352820)Q. 스튜디오드래곤 1분기 실적 전망은?A. 1분기 실적 컨센서스 소폭 하향 예상A. 하반기 대작 공개되며 주가 상승 기대Q. CJ ENM 1분기 실적 '어닝 쇼크' 기록하나?A. CJ ENM 1분기 부진한 실적 전망Q. 미디어 관련주 투자 전략 및 최선호주는?A. 1분기 광고 저점 예상, 스튜디오드래곤 추천이현지 유진투자증권 리서치센터 미디어엔터 애널리스트 by 매일경제TV                                                                                                                                                                                                                                                                                                                                                                                                                                                                

- 하나의 이슈를 다루지 않기에 감성평가가 불가능한 형태
- *****삭제*****

In [43]:
index_to_drop = news_nan.index[0]
news_nan = news_nan.drop(index_to_drop)

#### (4)

In [44]:
news_nan['SUMMARY_2'].iloc[0] 

'해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지난 2월 10일 지분인수 발표 당일 이수만 전 SM 총괄 프로듀서와 함께 내놓은 공동성명 이후 처음입니다.SM, 반박 자료 통해 조목조목 반박방 의장이 SM 인수에 대해 적대적 M&A가 아니라며 알리고 나서자 SM 측은 방 의장의 인터뷰 내용을 조목조목 반박했습니다.SM 측은 반박 자료를 통해 "방 의장이 적대적 M&A의 의미를 왜곡하고 있다"며 "방 의장은 적대적 M&A는 대주주 혹은 과점 주주의 의사에 반해서 회사를 시장에서 매집하는 것이라고 말햇는데, 적대적 M&A는 경영에 대한 법적 책임을 지는 이사회 동의 없이 강행하는 기업의 인수와 합병을 의미한다"고 지적했습니다.이어 "또한 적대적 M&A는 통상 공개매수나 위임장 대결의 형태를 취하는데, 현재 하이브가 시도하는 적대적 M&A 활동과 정확히 일치한다"고 꼬집었습니다.SM 측은 "방 의장은 ‘업계를 다 가져가려고 한다라는 부분에 대해 SM과 하이브가 한국에서 파는 CD 물량을 다 합쳐도 절대적으로 독점이 되기는 어렵다’고 말했지만 양사 결합 시에는 전체 시장 매출의 약 66%를 차지하는 독과점적 단일 기업군이 탄생하게 된다"며 "단일 기업 시장 독과점은 K팝의 다양성과 공정 경쟁을 저해하고 산업 경쟁력 저하로 이어지게 된다"고 비판했습니다.K팝의 성장을 위해 SM 인수전에 뛰어들었다는 방 의장의 입장을 정면 반박한 겁니다.아울러 SM 측은 "하이브는 그들이 지적한 SM 지배구조문제의 원인 제공자인 이수만 전 총괄과 손잡고 SM에 대한 적대적 M&A를 시도하고 있다"며 "결국 하이브의 적대적 M&A가 성공할 경우 또 다시 대주주만을 위한 SM으로 퇴행할 수 밖에 없다는 심각한 우려를 가지고 있다"고 덧붙였습니다.[윤혜주 디지털뉴스 기자 heyjude@mbn.co.kr]                                                                                                      

- 아래와 같이 수정함 

In [45]:
news_nan['SUMMARY_2'].iloc[0] = "해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지분인수 발표 당일 이수만 전 SM 총괄 프로듀서와 함께 내놓은 공동성명 이후 처음이다.방 의장이 SM 인수에 대해 적대적 M&A가 아니라며 알리고 나서자 SM 측은 방 의장의 인터뷰 내용을 조목조목 반박했습니다.SM 측은 반박 자료를 통해 -방 의장이 적대적 M&A의 의미를 왜곡하고 있다-며 -방 의장은 적대적 M&A는 대주주 혹은 과점 주주의 의사에 반해서 회사를 시장에서 매집하는 것이라고 말했는데, 적대적 M&A는 경영에 대한 법적 책임을 지는 이사회 동의 없이 강행하는 기업의 인수와 합병을 의미한다-고 지적했습니다.이어 -또한 적대적 M&A는 통상 공개매수나 위임장 대결의 형태를 취하는데, 현재 하이브가 시도하는 적대적 M&A 활동과 정확히 일치한다-고 꼬집었습니다.SM 측은 -방 의장은 ‘업계를 다 가져가려고 한다라는 부분에 대해 SM과 하이브가 한국에서 파는 CD 물량을 다 합쳐도 절대적으로 독점이 되기는 어렵다’고 말했지만 양사 결합 시에는 전체 시장 매출의 약 66%를 차지하는 독과점적 단일 기업군이 탄생하게 된다-며 -단일 기업 시장 독과점은 K팝의 다양성과 공정 경쟁을 저해하고 산업 경쟁력 저하로 이어지게 된다-고 비판했습니다.K팝의 성장을 위해 SM 인수전에 뛰어들었다는 방 의장의 입장을 정면 반박한 겁니다.아울러 SM 측은 -하이브는 그들이 지적한 SM 지배구조문제의 원인 제공자인 이수만 전 총괄과 손잡고 SM에 대한 적대적 M&A를 시도하고 있다-며 -결국 하이브의 적대적 M&A가 성공할 경우 또 다시 대주주만을 위한 SM으로 퇴행할 수 밖에 없다는 심각한 우려를 가지고 있다-고 덧붙였습니다."  


/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/139854289.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_nan['SUMMARY_2'].iloc[0] = "해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지분인수 발표 당일 이수만 전 SM 총괄 프로듀서와 함께 내놓은 공동성명 이후 처음이다.방 의장이 SM 인수에 대해 적대적 M&A가 아니라며 알리고 나서자 SM 측은 방 의장의 인터뷰 내용을 조목조목 반박했습니다.SM 측은 반박 자료를 통해 -방 의장이 적대적 M&A의 의미를 왜곡하고 있다-며 -방 의장은 적대적 M&A는 대주주 혹은 과점 주주의 의사에 반해서 회사를 시장에서 매집하는 것이라고 말했는데, 적대적 M&A는 경영에 대한 법적 책임을 지는 이사회 동의 없이 강행하는 기업의 인수와 합병을 의미한다-고 지적했습니다.이어 -또한 적대적 M&A는 통상 공개매수나 위임장 대결의 형태를 취하는데, 현재 하이브가 시도하는 적대적 M&A 활동과 정확히 일치한다-고 꼬집었습니다.SM 측은 -방 의장은 ‘업계를 다 가져가려고 한다라는 부분에 대해 SM과 하이브가 한국에서 파는 CD 물량을 다 합쳐도 절대적으로 독점이 되기는 어렵다’고 말했지만 양사 결합 시에는 전체 시장 매출의 약 66%를 차지하는 독과점적 단일 기업군이 탄생하게 된다-며 -단일 기업 시장 독과점은 K팝의 다양성과 공정 경쟁을 저해하고 산업 경쟁력 저하로 이어지게 된다-고 비판했습니다.K팝의 성장을 위해 SM 인수전에 뛰어들었다는 방 의장

#### (5)

In [46]:
news_nan['SUMMARY_2'].iloc[1] 

'-188억원(-26만주), 에코프로비엠 -170억원(-8만주), 에코프로 -167억원(-5만주), 대보마그네틱 -139억원(-18만주), 와이지엔터테인먼트 -42억원(-8만주), 동진쎄미켐 -36억원(-12만주), 디어유 -33억원(-8만주), 진성티이씨 -33억원(-30만주), 에치에프알 -29억원(-9만주), CJ ENM -28억원(-3만주), 이삭엔지니어링 -27억원(-22만주), 큐브엔터 -26억원(-14만주), 네오위즈 -24억원(-6만주), 에스피지 -23억원(-10만주), 상신이디피 -23억원(-10만주), 루트로닉 -20억원(-9만주), HPSP -18억원(-3만주), 이녹스첨단소재 -18억원(-5만주), 개인 투자자, 유가증권시장 순매수 1위~20위삼성SDI 147억원(2만주), NAVER 134억원(7만주), 카카오 120억원(21만주), SK하이닉스 87억원(10만주), 삼성중공업 84억원(167만주), 금양 60억원(13만주), POSCO홀딩스 43억원(1만주), 더존비즈온 42억원(9만주), GS건설 41억원(19만주), 강원랜드 40억원(22만주), 대덕전자 37억원(18만주), KT 37억원(13만주), 신풍제약 34억원(16만주), CJ제일제당 32억원(1만주), 신한지주 29억원(8만주), 롯데쇼핑 29억원(4만주), 한국조선해양 29억원(4만주), 메리츠금융지주 28억원(7만주), LG 26억원(3만주), 세방전지 25억원(5만주)개인 투자자, 유가증권시장 순매도 1위~20위삼성전자 -721억원(-120만주), LG에너지솔루션 -270억원(-5만주), 하이브 -267억원(-14만주), 삼성전기 -239억원(-16만주), 기아 -221억원(-28만주), SK이노베이션 -196억원(-11만주), LG전자 -127억원(-11만주), 셀트리온 -117억원(-8만주), 두산에너빌리티 -108억원(-61만주), 현대차 -99억원(-6만주), 카카오페이 -99억원(-16만주), 포스코케미칼 -99억원(-4만주), 현대차2우B -97억원(-

- *****삭제*****

In [47]:
index_to_drop = news_nan.index[1]
news_nan = news_nan.drop(index_to_drop)

#### (6)

In [48]:
news_nan['SUMMARY_2'].iloc[1] 

'올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를 기록할 것이라는 전망이 나오면서 엔터 관련 주들이 강세다.14일 마켓포인트에 따르면 오전 9시16분 현재 JYP Ent.(035900)는 전 거래일 대비 7.57% 오른 8만6800원에 거래되고 있다. 하이브(352820)는 3.47% 오른 25만3000원에 거래 중이고, 와이지엔터테인먼트(122870)와 에스엠(041510)도 각각 3.8%, 4.03% 오름세를 나타내고 있다.이는 최근 BTS 지민이 빌보드 싱글 차트 1위를 차지하고, 그룹 트와이스와 투모로우바이투게더가 빌보드 200차트에 머무는 등 글로벌 시장에서 K-pop이 약진을 하고 있기 때문인 것으로 풀이된다. 박성국 교보증권 연구원은 “엔터 4사의 올해 2분기 합산 앨범판매량과 콘서트 관객 수 모두 역대 최대 분기를 기록할 것으로 전망된다”라며 “주요 아티스트 컴백 몰리며 올해 2분기 엔터 4사 합산 앨범판매량 2210만장 기록할 것으로 예상된다”고 내다봤다.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

- 다음과 같이 수정

In [49]:
news_nan['SUMMARY_2'].iloc[1]  = "올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를 기록할 것이라는 전망이 나오면서 엔터 관련 주들이 강세다.14일 마켓포인트에 따르면 오전 9시16분 현재 JYP Ent.는 전 거래일 대비 7.57% 오른 8만6800원에 거래되고 있다. 하이브는 3.47% 오른 25만3000원에 거래 중이고, 와이지엔터테인먼트와 에스엠도 각각 3.8%, 4.03% 오름세를 나타내고 있다.이는 최근 BTS 지민이 빌보드 싱글 차트 1위를 차지하고, 그룹 트와이스와 투모로우바이투게더가 빌보드 200차트에 머무는 등 글로벌 시장에서 K-pop이 약진을 하고 있기 때문인 것으로 풀이된다. 박성국 교보증권 연구원은 “엔터 4사의 올해 2분기 합산 앨범판매량과 콘서트 관객 수 모두 역대 최대 분기를 기록할 것으로 전망된다”라며 “주요 아티스트 컴백 몰리며 올해 2분기 엔터 4사 합산 앨범판매량 2210만장 기록할 것으로 예상된다”고 내다봤다."                                       

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/4263125399.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_nan['SUMMARY_2'].iloc[1]  = "올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를 기록할 것이라는 전망이 나오면서 엔터 관련 주들이 강세다.14일 마켓포인트에 따르면 오전 9시16분 현재 JYP Ent.는 전 거래일 대비 7.57% 오른 8만6800원에 거래되고 있다. 하이브는 3.47% 오른 25만3000원에 거래 중이고, 와이지엔터테인먼트와 에스엠도 각각 3.8%, 4.03% 오름세를 나타내고 있다.이는 최근 BTS 지민이 빌보드 싱글 차트 1위를 차지하고, 그룹 트와이스와 투모로우바이투게더가 빌보드 200차트에 머무는 등 글로벌 시장에서 K-pop이 약진을 하고 있기 때문인 것으로 풀이된다. 박성국 교보증권 연구원은 “엔터 4사의 올해 2분기 합산 앨범판매량과 콘서트 관객 수 모두 역대 최대 분기를 기록할 것으로 전망된다”라며 “주요 아티스트 컴백 몰리며 올해 2분기 엔터 4사 합산 앨범판매량 2210만장 기록할 것으로 예상된다”고 내다봤다."


#### (7)

In [50]:
news_nan['SUMMARY_2'].iloc[2] 

"▶K팝 공연 확대…엔터주 ‘들썩’Q. BTS 군입대에도 건재한 하이브, 전망은?A. BTS 활동 없이도 견조한 외형 및 이익 성장A. 차별화되는 경쟁력은 'Weverse' 플랫폼A. 글로벌IP 확보와 다양한 서비스 확대A. 이익 레버리지 효과 2024년 극대화 될 것A. 견조한 성장 및 글로벌 플랫폼 이익 대비 저평가Q. 위버스 수익성, 성장 가능한가?A. 사업부 수직 계열화를 통한 수익성 내재화A. 외형이 커질수록 이익 레버리지 효과↑A. 고도화된 플랫폼 서비스 구축A. 아티스트 입점 확대A. 2024년 본격적인 수익 가시화될 것Q. 에스파 앨범 판매 사상 최고…에스엠 전망은?A. 에스엠 1분기 매출 2,039억원(+20.3%) A. 에스엠 영업이익 183억원(-5.0%)A. 에스엠 순이익 230억원(-10.0%)Q. 신인 걸그룹 공개…와이지 다시 주목받나?A. 와이지엔터 1분기 매출 1,575억원(+108.6%)A. 와이지엔터 영업이익 365억원(+497.6%)A. 와이지엔터 1분기 순이익 313억원(+437.5%)Q. 코스닥 시총 6위 오른 JYP Ent. 전망은?A. 1분기 매출액 866억원(+27.7%)A. 1분기 영업이익 266억원(+38.6%)A. 주목해야 할 그룹은 스트레이키즈A. 2018년 데뷔 이후 빠르게 성장A. 2022년 빌보드200 차트 진입과 동시에 1위 기록 A. 2022년 '글로벌 앨범 세일즈' 차트 TOP 10 진입A. 미국과 일본 지역 중심 팬덤 가파르게 성장 중Q. 부진의 늪에 빠진 CJ ENM, 전망은?A. CJ ENM 집중과 선택이 필요한 해A. 1분기 영업손실 적자 전환A. 연내 흑전 쉽지 않을 것으로 예상안진아 이베스트투자증권 리서치센터 엔터미디어 애널리스트 by 매일경제TV                                                                                                                                          

- 하나의 이슈를 다루지 않기에 감성평가가 불가능한 형태
- *****삭제*****

In [51]:
index_to_drop = news_nan.index[2]
news_nan = news_nan.drop(index_to_drop)

#### (8)

In [52]:
news_nan['SUMMARY_2'].iloc[2] 

'10일부터 11일까지 양일간 페스티벌 참여- 올림픽공원과 롯데호텔 월드에 전용 탑승지 마련- 위버스콘 페스티벌 참여 가수 노래 재생[이데일리 김현아 기자]타다(브이씨엔씨, 대표 이정행)가 10일부터 11일까지 양일간 서울 송파구 올림픽공원 KSPO 돔과 88 잔디마당에서 개최되는 2023 ‘Weverse Con Festival’ (이하 위버스콘 페스티벌)에 참여해 전 세계 케이팝 팬들의 콘서트장 이동을 책임졌다.하이브가 개최하는 ‘위버스콘 페스티벌’은 글로벌 팬덤 라이프 플랫폼 ‘위버스(Weverse)’의 다채로운 팬 경험을 오프라인에서 즐기며, 동시대 대중음악의 현주소를 종합적으로 경험할 수 있는 페스티벌이다. 이번 행사에는 그룹 뉴진스부터 투모로우바이투게더, 르세라핌, 지코, 효린 등 총 20개 팀이 참여하는 것으로 알려졌다.타다는 페스티벌 참가자를 위해 롯데호텔 월드 앞에 전용 탑승지를 마련하고 최대 5인까지 탑승할 수 있는 ‘타다 넥스트’ 차량으로 케이팝 팬들이 공연장을 오갈 수 있도록 했다.케이팝 팬들의 유쾌한 탑승 경험을 위해 차량 내부에서는 위버스콘 페스티벌에 참여하는 가수들의 플레이리스트가 재생된다. 이용자들이 전용 차량을 구분할 수 있도록 페스티벌 차량 외관은 위버스콘 페스티벌 아이콘으로 꾸며졌다.                                                                                                                                                                                                                                                                                                                                                                               

- 다음과 같이 수정

In [53]:
news_nan['SUMMARY_2'].iloc[2]  = "타다가 10일부터 11일까지 2023 ‘Weverse Con Festival’ (이하 위버스콘 페스티벌)에 참여해 전 세계 케이팝 팬들의 콘서트장 이동을 책임졌다.하이브가 개최하는 ‘위버스콘 페스티벌’은 글로벌 팬덤 라이프 플랫폼 ‘위버스(Weverse)’의 다채로운 팬 경험을 오프라인에서 즐기며, 동시대 대중음악의 현주소를 종합적으로 경험할 수 있는 페스티벌이다. 이번 행사에는 그룹 뉴진스부터 투모로우바이투게더, 르세라핌, 지코, 효린 등 총 20개 팀이 참여하는 것으로 알려졌다.타다는 페스티벌 참가자를 위해 롯데호텔 월드 앞에 전용 탑승지를 마련하고 최대 5인까지 탑승할 수 있는 ‘타다 넥스트’ 차량으로 케이팝 팬들이 공연장을 오갈 수 있도록 했다.케이팝 팬들의 유쾌한 탑승 경험을 위해 차량 내부에서는 위버스콘 페스티벌에 참여하는 가수들의 플레이리스트가 재생된다. 이용자들이 전용 차량을 구분할 수 있도록 페스티벌 차량 외관은 위버스콘 페스티벌 아이콘으로 꾸며졌다."     

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/3314436879.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_nan['SUMMARY_2'].iloc[2]  = "타다가 10일부터 11일까지 2023 ‘Weverse Con Festival’ (이하 위버스콘 페스티벌)에 참여해 전 세계 케이팝 팬들의 콘서트장 이동을 책임졌다.하이브가 개최하는 ‘위버스콘 페스티벌’은 글로벌 팬덤 라이프 플랫폼 ‘위버스(Weverse)’의 다채로운 팬 경험을 오프라인에서 즐기며, 동시대 대중음악의 현주소를 종합적으로 경험할 수 있는 페스티벌이다. 이번 행사에는 그룹 뉴진스부터 투모로우바이투게더, 르세라핌, 지코, 효린 등 총 20개 팀이 참여하는 것으로 알려졌다.타다는 페스티벌 참가자를 위해 롯데호텔 월드 앞에 전용 탑승지를 마련하고 최대 5인까지 탑승할 수 있는 ‘타다 넥스트’ 차량으로 케이팝 팬들이 공연장을 오갈 수 있도록 했다.케이팝 팬들의 유쾌한 탑승 경험을 위해 차량 내부에서는 위버스콘 페스티벌에 참여하는 가수들의 플레이리스트가 재생된다. 이용자들이 전용 차량을 구분할 수 있도록 페스티벌 차량 외관은 위버스콘 페스티벌 아이콘으로 꾸며졌다."


In [54]:
# 감정지수에 결측치가 있는 데이터들을 전처리한 결과 확인
news_nan

NEWS_YM        DATE_TIME  WRITER SUBCATEGORY  \
2468   202303  20230303_134044    매일경제          기술   
2701   202304  20230414_092237  eDaily          경제   
2861   202306  20230611_085817  eDaily          사회   

                                      TITLE  IMPORTANCE  \
2468  하이브의 SM 인수, '적대적 M&A' 성격 두고 방시혁·SM 충돌       29.27   
2701              [특징주]엔터株, K-팝 약진 속 일제히 강세       27.41   
2861           타다, 하이브 ‘위버스콘 페스티벌’서 K팝 팬 태워       24.31   

                       ITEM_NAME TAG_LIST  \
2468                         NaN   의사| 독점   
2701  JYP Ent.|하이브|와이지엔터테인먼트|에스엠      NaN   
2861                         NaN      NaN   

                                         PARSED CONTENT  LENGTH_SUM  \
2468  방시혁 하이브 의장이 미국 CNN 방송에 출연해 SM엔터테인먼트 인수전을 적대적 M...        2326   
2701  [이데일리 이용성 기자] 올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객...        2332   
2861  - 10일부터 11일까지 양일간 페스티벌 참여- 올림픽공원과 롯데호텔 월드에 전용 ...        2308   

                                                SUMMARY  \
2468  해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지난 2월 10일 지분인수 발...   
2701  올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를...   
2861  10일부터 11일까지 양일간 페스티벌 참여- 올림픽공원과 롯데호텔 월드에 전용 탑승...   

                                              SUMMARY_2 SENTIMENT_NEGATIVE  \
2468  해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지분인수 발표 당일 이수만 전...                NaN   
2701  올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를...                NaN   
2861  타다가 10일부터 11일까지 2023 ‘Weverse Con Festival’ (이...                NaN   

     SENTIMENT_NEUTRAL SENTIMENT_POSITIVE  
2468               NaN                NaN  
2701               NaN                NaN  
2861               NaN                NaN

### 전처리한 결측치 존재 데이터에 대해 다시 감정지수 구하기 

In [55]:
# 기본 세팅
#!/usr/bin/env python3

client_id = "5bgb8zehd8"
client_secret = "yunrcvpfGN1Lrw8TR1X8xTxt8Eem1fJGX4EzRoaT"
url="https://naveropenapi.apigw.ntruss.com/sentiment-analysis/v1/analyze"
headers = {
    "X-NCP-APIGW-API-KEY-ID": client_id,
    "X-NCP-APIGW-API-KEY": client_secret,
    "Content-Type": "application/json"
}


# 데이터프레임 생성
columns = ['SENTIMENT_NEGATIVE', 'SENTIMENT_NEUTRAL', 'SENTIMENT_POSITIVE'] # 감정 분석 결과를 데이터프레임에 추가할 열 이름
sent = pd.DataFrame(columns=columns) # 감정 분석 결과를 저장할 데이터프레임

for i in range(len(news_nan)):
    content = news_nan['SUMMARY_2'].iloc[i] # 감성분석할 내용 : news 데이터의 SUMMARY_2 내용 전체 
    data = {
      "content": content
    }
    print(json.dumps(data, indent=4, sort_keys=True))
    response = requests.post(url, data=json.dumps(data), headers=headers)
    rescode = response.status_code
    if(rescode == 200):
        print (response.text)
        response_data = json.loads(response.text)
        A = response_data["document"]["confidence"]["negative"] # 각 요약문의 부정지수 
        B = response_data["document"]["confidence"]["neutral"] # 각 요약문의 중립지수 
        C = response_data["document"]["confidence"]["positive"] # 각 요약문의 긍정지수 
        sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
        # 부정지수, 중립지수, 긍정지수를 각각 sent 데이터프레임의 SENTIMENT_NEGATIVE, SENTIMENT_NEUTRAL, SENTIMENT_POSITIVE 변수에 저장
        
    else:
        print("Error : " + response.text) 
        sent = sent.append({'SENTIMENT_NEGATIVE': np.nan, 'SENTIMENT_NEUTRAL': np.nan, 'SENTIMENT_POSITIVE': np.nan}, ignore_index=True)
        # 감정분석 결과가 산출되지 않는 경우 각 변수에 np.nan 값을 할당
        

{
    "content": "\ud574\uc678 \uc5b8\ub860 \uc778\ud130\ubdf0\ub97c \ud1b5\ud574 \ubc29 \uc758\uc7a5\uc758 \uc785\uc7a5\uc774 \uc54c\ub824\uc9c4 \uac74 \uc9c0\ubd84\uc778\uc218 \ubc1c\ud45c \ub2f9\uc77c \uc774\uc218\ub9cc \uc804 SM \ucd1d\uad04 \ud504\ub85c\ub4c0\uc11c\uc640 \ud568\uaed8 \ub0b4\ub193\uc740 \uacf5\ub3d9\uc131\uba85 \uc774\ud6c4 \ucc98\uc74c\uc774\ub2e4.\ubc29 \uc758\uc7a5\uc774 SM \uc778\uc218\uc5d0 \ub300\ud574 \uc801\ub300\uc801 M&A\uac00 \uc544\ub2c8\ub77c\uba70 \uc54c\ub9ac\uace0 \ub098\uc11c\uc790 SM \uce21\uc740 \ubc29 \uc758\uc7a5\uc758 \uc778\ud130\ubdf0 \ub0b4\uc6a9\uc744 \uc870\ubaa9\uc870\ubaa9 \ubc18\ubc15\ud588\uc2b5\ub2c8\ub2e4.SM \uce21\uc740 \ubc18\ubc15 \uc790\ub8cc\ub97c \ud1b5\ud574 -\ubc29 \uc758\uc7a5\uc774 \uc801\ub300\uc801 M&A\uc758 \uc758\ubbf8\ub97c \uc65c\uace1\ud558\uace0 \uc788\ub2e4-\uba70 -\ubc29 \uc758\uc7a5\uc740 \uc801\ub300\uc801 M&A\ub294 \ub300\uc8fc\uc8fc \ud639\uc740 \uacfc\uc810 \uc8fc\uc8fc\uc758 \uc758\uc0ac\uc5d0 \ubc18\ud574\

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/4212089362.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)
/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/4212089362.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)


{"document":{"sentiment":"positive","confidence":{"negative":0.0123429755,"positive":54.70151,"neutral":45.286148}},"sentences":[{"content":"타다가 10일부터 11일까지 2023 ‘Weverse Con Festival’ (이하 위버스콘 페스티벌)에 참여해 전 세계 케이팝 팬들의 콘서트장 이동을 책임졌다.","offset":0,"length":91,"sentiment":"neutral","confidence":{"negative":2.883632E-4,"positive":4.350354E-4,"neutral":0.9992766},"highlights":[{"offset":60,"length":30}]},{"content":"하이브가 개최하는 ‘위버스콘 페스티벌’은 글로벌 팬덤 라이프 플랫폼 ‘위버스(Weverse)’의 다채로운 팬 경험을 오프라인에서 즐기며, 동시대 대중음악의 현주소를 종합적으로 경험할 수 있는 페스티벌이다.","offset":91,"length":114,"sentiment":"positive","confidence":{"negative":2.5522526E-4,"positive":0.99169767,"neutral":0.00804712},"highlights":[{"offset":77,"length":36}]},{"content":" 이번 행사에는 그룹 뉴진스부터 투모로우바이투게더, 르세라핌, 지코, 효린 등 총 20개 팀이 참여하는 것으로 알려졌다.","offset":205,"length":67,"sentiment":"neutral","confidence":{"negative":1.1103425E-4,"positive":2.63533E-4,"neutral":0.9996253},"highlights":[{"offset":50,"length":16}]},{"content":"타다는 페스티벌 참가자를 위해 롯데호텔 월드 앞에 전용 탑승지를

/var/folders/4t/dyhc70gd7zjdwxdh7x7f77240000gn/T/ipykernel_96800/4212089362.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent = sent.append({'SENTIMENT_NEGATIVE': A, 'SENTIMENT_NEUTRAL': B, 'SENTIMENT_POSITIVE': C}, ignore_index=True)


In [56]:
# 감정분석 결과 데이터프레임 확인
sent

SENTIMENT_NEGATIVE SENTIMENT_NEUTRAL SENTIMENT_POSITIVE
0          95.182945          4.809798           0.007258
1           0.024469           0.03598           99.93955
2           0.012343         45.286148           54.70151

In [57]:
# 기존의 news_nan 에서 감성지수 변수 제거 
news_nan = news_nan.drop(['SENTIMENT_NEGATIVE','SENTIMENT_NEUTRAL','SENTIMENT_POSITIVE'], axis=1)

In [58]:
# 기존의 news_nan 에서 인덱스 초기화
news_nan.reset_index(drop=True, inplace=True)

In [59]:
# news_nan에 감성지수 데이터프레임(sent) 합치기
news_nan = pd.concat([news_nan, sent], axis=1)
news_nan # 확인

NEWS_YM        DATE_TIME  WRITER SUBCATEGORY  \
0   202303  20230303_134044    매일경제          기술   
1   202304  20230414_092237  eDaily          경제   
2   202306  20230611_085817  eDaily          사회   

                                   TITLE  IMPORTANCE  \
0  하이브의 SM 인수, '적대적 M&A' 성격 두고 방시혁·SM 충돌       29.27   
1              [특징주]엔터株, K-팝 약진 속 일제히 강세       27.41   
2           타다, 하이브 ‘위버스콘 페스티벌’서 K팝 팬 태워       24.31   

                    ITEM_NAME TAG_LIST  \
0                         NaN   의사| 독점   
1  JYP Ent.|하이브|와이지엔터테인먼트|에스엠      NaN   
2                         NaN      NaN   

                                      PARSED CONTENT  LENGTH_SUM  \
0  방시혁 하이브 의장이 미국 CNN 방송에 출연해 SM엔터테인먼트 인수전을 적대적 M...        2326   
1  [이데일리 이용성 기자] 올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객...        2332   
2  - 10일부터 11일까지 양일간 페스티벌 참여- 올림픽공원과 롯데호텔 월드에 전용 ...        2308   

                                             SUMMARY  \
0  해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지난 2월 10일 지분인수 발...   
1  올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를...   
2  10일부터 11일까지 양일간 페스티벌 참여- 올림픽공원과 롯데호텔 월드에 전용 탑승...   

                                           SUMMARY_2 SENTIMENT_NEGATIVE  \
0  해외 언론 인터뷰를 통해 방 의장의 입장이 알려진 건 지분인수 발표 당일 이수만 전...          95.182945   
1  올해 2분기 국내 엔터주들의 합산 앨범판매량과 콘서트 관객수 모두 역대 최대 분기를...           0.024469   
2  타다가 10일부터 11일까지 2023 ‘Weverse Con Festival’ (이...           0.012343   

  SENTIMENT_NEUTRAL SENTIMENT_POSITIVE  
0          4.809798           0.007258  
1           0.03598           99.93955  
2         45.286148           54.70151

## 최종 감성지수 데이터프레임 생성

### 데이터프레임 병합

- 감성지수가 결측이 아닌 행들(np_no_nan) 과 감성지수에 결측이 있어 전처리한 행들(np_nan)을 세로로 합친다

In [60]:
combined_news = pd.concat([news_nan, news_no_nan], ignore_index=True)

In [61]:
combined_news.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2889 entries, 0 to 2888
Data columns (total 15 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   NEWS_YM             2889 non-null   int64  
 1   DATE_TIME           2889 non-null   object 
 2   WRITER              2889 non-null   object 
 3   SUBCATEGORY         2889 non-null   object 
 4   TITLE               2889 non-null   object 
 5   IMPORTANCE          2889 non-null   float64
 6   ITEM_NAME           1556 non-null   object 
 7   TAG_LIST            2225 non-null   object 
 8   PARSED CONTENT      2889 non-null   object 
 9   LENGTH_SUM          2889 non-null   int64  
 10  SUMMARY             2889 non-null   object 
 11  SUMMARY_2           2889 non-null   object 
 12  SENTIMENT_NEGATIVE  2889 non-null   object 
 13  SENTIMENT_NEUTRAL   2889 non-null   object 
 14  SENTIMENT_POSITIVE  2889 non-null   object 
dtypes: float64(1), int64(2), object(12)
memory usage: 338.7

### 데이터 저장

In [62]:
# 감성변수가 추가된 데이터를 xlsx 파일로 저장
excel_filename = '../../../data/News/news_sentiment_final.xlsx'
combined_news.to_excel(excel_filename, index=False)